# 2 (primera parte)

In [7]:
var('a')
cp = [a,-a-1,1]
cq = [-a-1/12,-a+8/12,a+5/12]

In [8]:
# Estabilidad:
p(x) = cp[2]*x^2+cp[1]*x+cp[0]
solve(p(x) == 0 ,x) # Condición de la raíz si a está en [-1,1)

[x == a, x == 1]

In [9]:
[k*cp[k] for k in [0..2]]

[0, -a - 1, 2]

In [10]:
C0 = sum(cp)
C1 = sum([k*cp[k] for k in [0..2]]) - sum(cq)
C0, C1 # Siempre es consistente

(0, 0)

In [11]:
[k^2*cp[k] for k in [0..2]],[k*cq[k] for k in [0..2]]

([0, -a - 1, 4], [0, -a + 2/3, 2*a + 5/6])

In [12]:
C2 = sum([k^2*cp[k] for k in [0..2]])/2 - sum([k*cq[k] for k in [0..2]])
C2 # Para que sea de orden 2, tiene que ser a = 0

-3/2*a

In [13]:
C3 = sum([k^3*cp[k] for k in [0..2]])/6 - sum([k^2*cq[k] for k in [0..2]])/2
C3 # Orden 3 si a = 0 (es el método de Adams-Moulton)

-5/3*a

In [14]:
C4 = sum([k^4*cp[k] for k in [0..2]])/24 - sum([k^3*cq[k] for k in [0..2]])/6
C4 # No es de orden 4

-29/24*a - 1/24

In [15]:
p(x,a=1/2), p(x,a=1/2).roots()

(x^2 - 3/2*x + 1/2, [(1, 1), (1/2, 1)])

# 1 (segunda parte)

Queremos calcular $\sum_{n=0}^m x_n$. Para ello basta resolver $\Delta F(n) = x_n$, pero
$$
x_n = x_{n+2}+x_{n+1},
$$
Luego $F(n) = x_{n+1}$ y
$$
\sum_{n=0}^m x_n = x_{m+2}-x_{0+1}. 
$$

In [16]:
@cached_function
def fibo(n):
    if n<=1:
        return n
    return fibo(n-1) + fibo(n-2)

In [17]:
# Comprobamos
m = 30
sum([fibo(n) for n in [0 .. m]]), fibo(m+2)-fibo(1)

(2178308, 2178308)

El apartado anterior no depende de las condicione iniciales. Así que para determinar las condiciones iniciales que hacen sumable la serie, basta obtener las condiciones iniciales que hacen que la sucesión esté acotada. 

In [18]:
# Obtenemos las raíces del polinomio característico
(x^2-x-1).roots()

[(-1/2*sqrt(5) + 1/2, 1), (1/2*sqrt(5) + 1/2, 1)]

Las soluciones son de la forma
$$
x_n = a \left(\frac{1+\sqrt{5}}{2}\right)^n + b\left(\frac{1-\sqrt{5}}{2}\right)^n
$$
Así que será sumable si $a=0$, es decir, $x_0 = b$, $x_1 = b(1-\sqrt{5})/2$, para cualquier $b\in\mathbb{R}$.

In [19]:
@cached_function
def fibo2(n):
    b = 1 
    if n==0:
        return b
    if n==1:
        return b*(1-sqrt(5))/2
    return fibo2(n-1) + fibo2(n-2)

In [20]:
# Comprobamos. 
m = 20
sum([fibo2(n) for n in [0 .. m]]).n() 

0.618059239361173

# 2 (segunda parte)

In [42]:
# Copiamos las funciones de la práctica
def derivada_total(f,k):
    derivada = copy(f)
    for i in range(k):
        derivada = derivada.diff() * f
    return derivada
def phi_taylor(f,h,k):
    return sum([ derivada_total(f,i)*h^i/factorial(i+1) 
                     for i in [0 .. k-1 ]])
def taylor(f,x0,h,n,k):
    xi = [vector(RDF,x0)]*(n+1)
    T = phi_taylor(f,h,k)
    for i in [ 1 .. n ]:
        xi[i] = xi[i-1] + h * T( *xi[i-1] ) 
    return xi

In [43]:
F(x,y) = [y,-x] # Sistema equivalente
phi_taylor(F,0.1,3) # Función phi

(x, y) |--> (-0.0500000000000000*x + 0.998333333333333*y, -0.998333333333333*x - 0.0500000000000000*y)

In [44]:
# Aplicamos dos pasos del método de Taylor
xi = taylor(F,vector(RDF,[0,1]),1/10,2,3)
xi

[(0.0, 1.0),
 (0.09983333333333333, 0.995),
 (0.19866833333333334, 0.9800583055555555)]

In [45]:
@cached_function
def beta_Adams_Bashforth(k,j):
    # Coeficiente j del método de Adams-Bashforth de k-pasos.
    lj(t)=prod([(t-i)/(j-i) for i in [0..j-1]+[j+1..k-1]])    
    return lj.integral(t,k-1,k)

In [46]:
@cached_function
def beta_Adams_Moulton(k,j):
    # Coeficiente j del método de Adams-Bashforth de k-pasos.
    lj(t)=prod([(t-i)/(j-i) for i in [0..j-1]+[j+1..k]])    
    return lj.integral(t,k-1,k)

In [47]:
# Copiamos el predictor-corrector (versión sistemas que habremos hecho para resolver los ejercicios - también se podría hacer "a mano" porque son dos pasos)
def PCA3(f,x0,h,m):
    # Creamos las listas iniciales donde guardaremos los valores
    xk = x0 + [ x0[0] ]*(m-2)
    for n in [0 .. m-3]:
        # Adams-Basforth
        xk[n+3] = xk[n+2] + h*(23*f(*xk[n+2]) 
                              -16*f(*xk[n+1])  
                              +5*f(*xk[n]))/12
        xktilde = copy(xk[n+3])
        print('Predictor',xktilde) # Imprimimos el corrector
        # Adams-Moulton
        xk[n+3] = xk[n+2] + h*(5*f(*xk[n+3]) 
                              +8*f(*xk[n+2])  
                                -f(*xk[n+1]))/12
        print('Corrector',xk[n+3]) # Imprimimos el corrector
        print('Error', (xktilde-xk[n+3])*0.1 ) # imprimimos la estimación del error (puede ser en norma)
    return xk

In [48]:
PCA3(F,xi,1/10,4)

Predictor (0.29551284189814814, 0.9552913194444443)
Corrector (0.2955176920138889, 0.9553326593653549)
Error (-4.850115740751004e-07, -4.133992091059913e-06)
Predictor (0.3894070109848412, 0.9210211572849152)
Corrector (0.38941526497882106, 0.9210617572178385)
Error (-8.253993979856489e-07, -4.059993292326869e-06)


[(0.0, 1.0),
 (0.09983333333333333, 0.995),
 (0.19866833333333334, 0.9800583055555555),
 (0.2955176920138889, 0.9553326593653549),
 (0.38941526497882106, 0.9210617572178385)]

In [49]:
xi

[(0.0, 1.0),
 (0.09983333333333333, 0.995),
 (0.19866833333333334, 0.9800583055555555)]

In [50]:
x0 = vector(RDF,[0,1])
x1 = vector(RDF,(0.09983333333333333, 0.995))
x2 = vector(RDF, (0.19866833333333334, 0.9800583055555555))
x0,x1,x2

((0.0, 1.0),
 (0.09983333333333333, 0.995),
 (0.19866833333333334, 0.9800583055555555))

In [52]:
h = 0.1
x3b = x2 +  h*(23*F(*x2)-16*F(*x1)+5*F(*x0))/12
x3b

(0.29551284189814814, 0.9552913194444443)

In [53]:
x3 = x2 +  h*(5*F(*x3b)+8*F(*x2)-F(*x1))/12
x3

(0.2955176920138889, 0.9553326593653549)

In [54]:
(x3-x3b)/10

(4.850115740751004e-07, 4.133992091059913e-06)

# 3 (segunda parte)

## a)

In [28]:
# Escribimos nuestra ecuación en forma de sistema u'=v, v'= u - cos(t)
var('t,u,v')
eqns=[v,u-cos(t)]

In [29]:
# Resolvemos el PVI u(0)=0, u'(0)=-1
P=desolve_system_rk4(eqns,[u,v],ics=[0,0,-1],ivar=t,end_points=1,step=0.01)
# Sólo necesitamos el valor aproximado de u(1)
v0 = -1
phi0=P[-1][1]
phi0

-1.676590357925592

In [30]:
# Resolvemos el PVI u(0)=0, u'(0)=1
P=desolve_system_rk4(eqns,[u,v],ics=[0,0,1],ivar=t,end_points=1,step=0.01)
# Sólo necesitamos el valor aproximado de u(1)
v1 = 1
phi1=P[-1][1]
phi1

0.6738120291064539

In [31]:
# Calculamos v2
v2 = ( v0*phi1 - v1*phi0 )/( phi1 - phi0 )
v2

0.42664112934525633

In [32]:
# Calculamos phi2 # Como es lineal deberíamos haber obtenido la solución y phi2 debería valer 0
P=desolve_system_rk4(eqns,[u,v],ics=[0,0,v2],ivar=t,end_points=1,step=0.01)
phi2 = P[-1][1]
phi2 # Como es prácticamente 0, hemos terminado. Se puede calcular un paso más, pero volveremos a obtener el mismo valor

-1.31405303305243e-16

## b)

In [55]:
# Función que define los coeficientes del sistema (se puede hacer a mano si no se tenía resuelta en el ejercicio 2)
# Función que define los coeficientes del sistema
def a(i,j,h):
    if i==j:
        return 2 + h^2
    if abs(i-j)==1:
        return -1
    else:
        return 0

In [56]:
# Planteamos el sistema y lo resolvemos
N = 5
h = 1/(N+1)
A = h^-2*matrix(RDF,[[a(i,j,h) for j in [1 .. N]] for i in [1 .. N]],sparse=true)
F = vector(RDF,[ cos(j*h)  for j in [1..N]])

In [57]:
show(A,F) # Sistema

[ 73.0 -36.0   0.0   0.0   0.0]
[-36.0  73.0 -36.0   0.0   0.0]
[  0.0 -36.0  73.0 -36.0   0.0]
[  0.0   0.0 -36.0  73.0 -36.0]
[  0.0   0.0   0.0 -36.0  73.0] (0.986143231562925, 0.9449569463147377, 0.8775825618903728, 0.785887260776948, 0.6724122440830567)

In [58]:
# Resolvemos el sistema
ui=A.solve_right(F)
# Representamos las soluciones
ui # Soluciones

(0.05755871399438261, 0.08932341361186126, 0.09732051509870444, 0.08364367084133463, 0.05046006019686443)